# IMDB Wiki

- <https://data.vision.ee.ethz.ch/cvl/rrothe/imdb-wiki/>
- figure out .mat metadata
- create identity list
- augment with knowledge graph data

In [1]:
%reload_ext autoreload
%autoreload 2

import os
from os.path import join
from glob import glob
from random import randint
from pathlib import Path

import numpy as np
import pandas as pd
import cv2 as cv
%matplotlib inline
import matplotlib.pyplot as plt

import sys
sys.path.append('/work/megapixels_dev/megapixels/')
from app.settings import app_cfg as cfg
from app.settings import types
from app.utils import im_utils, file_utils
from app.models.bbox import BBox
from app.models.data_store import DataStore
from app.processors import face_detector, face_extractor

from app.models.bbox import BBox

In [2]:
data_store = DataStore(types.DataStore.HDD, types.Dataset.IMDB_WIKI)

## Files

In [4]:
fp_records = data_store.metadata(types.Metadata.FILE_RECORD)
#df_records = pd.read_csv(fp_records, dtype={'fn':str}).set_index('index')

fp_roi = data_store.metadata(types.Metadata.FACE_ROI)
#df_roi = pd.read_csv(fp_roi).set_index('index')

fp_vector = data_store.metadata(types.Metadata.FACE_VECTOR)
#df_vector = pd.read_csv(fp_vector).set_index('index')

### Load metadata

In [31]:
from scipy.io import loadmat
metadata = loadmat('/data_store_hdd/datasets/people/imdb_wiki/imdb/imdb.mat')
print(metadata.keys())
metadata = metadata['imdb']

dict_keys(['__header__', '__version__', '__globals__', 'imdb'])


In [32]:
metadata = metadata[0][0]

In [30]:
print(len(metadata))

1


In [79]:
# 0: numbers from 47 to 734963
# 1: numbers 1961 to 2015
# 2: filepaths
# 3: 0.0 or 1.0 (gender?)
# 4: names, 460723 length
# 5: 
print(metadata[5][0][0], len(metadata[5][0]), type(metadata[5][0]))
a = metadata[5][0]
print(a.min())

[[1072.926  161.838 1214.784  303.696]] 460723 <class 'numpy.ndarray'>


ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [29]:
print(
  metadata[0][0][0])
print(metadata[0][0][0])

[693726 693726 693726 ... 726831 726831 726831]


IndexError: index 1 is out of bounds for axis 0 with size 1

```
 For both the IMDb and Wikipedia images we provide a separate .mat file which can be loaded with Matlab containing all the meta information. The format is as follows:

    dob: date of birth (Matlab serial date number)
    photo_taken: year when the photo was taken
    full_path: path to file
    gender: 0 for female and 1 for male, NaN if unknown
    name: name of the celebrity
    face_location: location of the face. To crop the face in Matlab run

    img(face_location(2):face_location(4),face_location(1):face_location(3),:))

    face_score: detector score (the higher the better). Inf implies that no face was found in the image and the face_location then just returns the entire image
    second_face_score: detector score of the face with the second highest score. This is useful to ignore images with more than one face. second_face_score is NaN if no second face was detected.
    celeb_names (IMDB only): list of all celebrity names
    celeb_id (IMDB only): index of celebrity name

The age of a person can be calculated based on the date of birth and the time when the photo was taken (note that we assume that the photo was taken in the middle of the year):

[age,~]=datevec(datenum(wiki.photo_taken,7,1)-wiki.dob); 
```

In [107]:
imdb_data = []
for i, v in enumerate(k):
  print(i, v.shape, v[0])
  if i != 8:
    print(v[0])
  else:

0 (1, 460723) [693726 693726 693726 ... 726831 726831 726831]
1 (1, 460723) [1968 1970 1968 ... 2011 2011 2011]
2 (1, 460723) [array(['01/nm0000001_rm124825600_1899-5-10_1968.jpg'], dtype='<U43')
 array(['01/nm0000001_rm3343756032_1899-5-10_1970.jpg'], dtype='<U44')
 array(['01/nm0000001_rm577153792_1899-5-10_1968.jpg'], dtype='<U43') ...
 array(['08/nm3994408_rm926592512_1989-12-29_2011.jpg'], dtype='<U44')
 array(['08/nm3994408_rm943369728_1989-12-29_2011.jpg'], dtype='<U44')
 array(['08/nm3994408_rm976924160_1989-12-29_2011.jpg'], dtype='<U44')]
3 (1, 460723) [1. 1. 1. ... 0. 0. 0.]
4 (1, 460723) [array(['Fred Astaire'], dtype='<U12')
 array(['Fred Astaire'], dtype='<U12')
 array(['Fred Astaire'], dtype='<U12') ...
 array(['Jane Levy'], dtype='<U9') array(['Jane Levy'], dtype='<U9')
 array(['Jane Levy'], dtype='<U9')]
5 (1, 460723) [array([[1072.926,  161.838, 1214.784,  303.696]])
 array([[477.184, 100.352, 622.592, 245.76 ]])
 array([[114.96964309, 114.96964309, 451.68657236, 451.

IndexError: index 1 is out of bounds for axis 0 with size 1

In [104]:
# k[8] is names
for v in k[8][0]:
  print(v)

["'Lee' George Quinones"]
["'Weird Al' Yankovic"]
['2 Chainz']
['50 Cent']
['A Martinez']
['A.D. Miles']
['A.J. Buckley']
['A.J. Cook']
['A.J. Johnson']
['A.J. Langer']
['A.J. McLean']
['A.J. Saudin']
['A.J. Trauth']
['A.R. Rahman']
['AJ Bowen']
['AJ Michalka']
['Aaliyah']
['Aamir Khan']
['Aaron Abrams']
['Aaron Ashmore']
['Aaron Carter']
['Aaron Christian Howles']
['Aaron Coady']
['Aaron D. Spears']
['Aaron Douglas']
['Aaron Eckhart']
['Aaron Farb']
['Aaron Franklin']
['Aaron Hill']
['Aaron Himelstein']
['Aaron Jackson']
['Aaron Jay Rome']
['Aaron Katz']
['Aaron Kwok']
['Aaron Lohr']
['Aaron Lustig']
['Aaron McCusker']
['Aaron Michael Davies']
['Aaron Michael Metchik']
['Aaron Norris']
['Aaron Paul']
['Aaron Pearl']
['Aaron Pedersen']
['Aaron Rodgers']
['Aaron Ruell']
['Aaron Russo']
['Aaron Schwartz']
['Aaron Seltzer']
['Aaron Sorkin']
['Aaron Spelling']
['Aaron Stanford']
['Aaron Taylor-Johnson']
['Aaron Tveit']
['Aaron Wolff']
['Aaron Woodley']
['Aaron Yoo']
['Aaron Zigman']
['Aash

['Andi Vasluianu']
['Andie MacDowell']
['Andra Fuller']
['Andre Braugher']
['Andre Gower']
['Andre Royo']
['Andre Schneider']
['Andrea Allan']
['Andrea Anders']
['Andrea Arnold']
['Andrea Barber']
['Andrea Bendewald']
['Andrea Bocelli']
['Andrea Bogart']
['Andrea Bosca']
['Andrea Bowen']
['Andrea Brooks']
['Andrea Corr']
['Andrea Di Stefano']
['Andrea Elson']
['Andrea Evans']
['Andrea Gabriel']
['Andrea Lewis']
['Andrea Lowe']
['Andrea Lui']
['Andrea Marcovicci']
['Andrea Martin']
['Andrea Montenegro']
['Andrea Morris']
['Andrea Occhipinti']
['Andrea Osvárt']
['Andrea Parker']
['Andrea Powell']
['Andrea Riseborough']
['Andrea Roth']
['Andrea Savage']
['Andrea Stefancikova']
['Andreas Dresen']
['Andreas Günther']
['Andreas Katsulas']
['Andreas Prochaska']
['Andreas Wisniewski']
['Andrei Arlovski']
['Andrei Claude']
['Andrew Adamson']
['Andrew Airlie']
['Andrew Bergman']
['Andrew Bryniarski']
['Andrew Buchan']
['Andrew Bujalski']
['Andrew Caldwell']
['Andrew Clarke']
['Andrew Daly']
['An

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)




['Bill Pullman']
['Bill Quinn']
['Bill Romanowski']
['Bill Sage']
['Bill Simmons']
['Bill Skarsgård']
['Bill Smitrovich']
['Bill Stinchcomb']
['Bill Travers']
['Bill Walton']
['Bill Withers']
['Bill Wyman']
['Bille August']
['Billi Bruno']
['Billie Jean King']
['Billie Joe Armstrong']
['Billie Lourd']
['Billie Piper']
['Billie Whitelaw']
['Billy Aaron Brown']
['Billy Barty']
['Billy Blanks']
['Billy Bob Thornton']
['Billy Boyd']
['Billy Burke']
['Billy Bush']
['Billy Campbell']
['Billy Connolly']
['Billy Corgan']
['Billy Crudup']
['Billy Crystal']
['Billy Curtis']
['Billy Dee Williams']
['Billy Drago']
['Billy Gallo']
['Billy Gardell']
['Billy Gibbons']
['Billy Green Bush']
['Billy Idol']
['Billy Joel']
['Billy L. Sullivan']
['Billy Lockwood']
['Billy Lush']
['Billy Magnussen']
['Billy Mays']
['Billy Miller']
['Billy Murray']
['Billy Porter']
['Billy Preston']
['Billy Ray Cyrus']
['Billy Rosemberg']
['Billy Sands']
['Billy Unger']
['Billy Warlock']
['Billy Wilder']
['Billy Wirth']
['B

['Carolina Bermudez']
['Carolina Crescentini']
['Carolina Hoyos']
['Caroline Aaron']
['Caroline Bliss']
['Caroline Carver']
['Caroline Chikezie']
["Caroline D'Amore"]
['Caroline Dhavernas']
['Caroline Ducey']
['Caroline Goodall']
['Caroline Kennedy']
['Caroline Lagerfelt']
['Caroline Manzo']
['Caroline Maria Winberg']
['Caroline Munro']
['Caroline Reitman']
['Caroline Rhea']
['Caroline Sunshine']
['Caroline Tillette']
['Caroline Williams']
['Caroll Spinney']
['Carolyn Conwell']
['Carolyn Hennesy']
['Carolyn Jones']
['Carolyn Lawrence']
['Carolyn Murphy']
['Carolyn Pickles']
['Carolyn Purdy-Gordon']
['Carrie Ann Inaba']
['Carrie Brownstein']
['Carrie Coon']
['Carrie Finklea']
['Carrie Fisher']
['Carrie Genzel']
['Carrie Henn']
['Carrie Keagan']
['Carrie Lorraine']
['Carrie MacLemore']
['Carrie Preston']
['Carrie Snodgress']
['Carrie Underwood']
['Carrie-Anne Moss']
['Carroll Baker']
['Carroll Ballard']
["Carroll O'Connor"]
['Carré Otis']
['Carsen Flowers']
['Carson Brown']
['Carson Daly

...

['Jane Carr']
['Jane Curtin']
['Jane Espenson']
['Jane Fallon']
['Jane Fonda']
['Jane Goldman']
['Jane Hajduk']
['Jane Horrocks']
['Jane Kaczmarek']
['Jane Krakowski']
['Jane Leeves']
['Jane Levy']
['Jane Lynch']
['Jane March']
['Jane McGregor']
['Jane Merrow']
['Jane Pauley']
['Jane Powell']
['Jane Rosenthal']
['Jane Russell']
['Jane Seymour']
['Jane Sibbett']
['Jane Wiedlin']
['Jane Wyatt']
['Janeane Garofalo']
['Janel Moloney']
['Janel Parrish']
['Janelle Monáe']
['Janelle Pierzina']
['Janet Evanovich']
['Janet Fielding']
['Janet Hubert']
['Janet Jackson']
['Janet Jones']
['Janet Leigh']
['Janet McTeer']
['Janet Montgomery']
['Janet Suzman']
['Janette Manrara']
['Janette Scott']
['Janice Crystal']
['Janice Dickinson']
['Janice Lynde']
['Janice Rule']
['Janin Reinhardt']
['Janina Gavankar']
['Janine Turner']
['Janis Joplin']
['Jann Arden']
['Jann Carl']
['Jann Wenner']
['Jansen Panettiere']
['January Jones']
['Janusz Kaminski']
['Jareb Dauplaise']
['Jared Fogle']
['Jared Followill']


['Jodi Long']
["Jodi Lyn O'Keefe"]
['Jodi Picoult']
['Jodi Thelen']
['Jodie Foster']
['Jodie Markell']
['Jodie Sweetin']
['Jodie Whittaker']
['Jody Thompson']
['Jody Watley']
['Joe Anderson']
['Joe Armstrong']
['Joe Basile']
['Joe Berlinger']
['Joe Biden']
['Joe Breen']
['Joe Carnahan']
['Joe Cobden']
['Joe Cole']
['Joe Cornish']
['Joe Costner']
['Joe Dallesandro']
['Joe Dante']
['Joe Dempsie']
['Joe Dinicol']
['Joe Dixon']
['Joe Don Baker']
['Joe Duer']
['Joe E. Tata']
['Joe Egender']
['Joe Elliott']
['Joe Estevez']
['Joe Eszterhas']
['Joe Farina']
['Joe Flaherty']
['Joe Flanigan']
['Joe Frazier']
['Joe Hammerstone']
['Joe Hill']
['Joe Jackson']
['Joe Johnston']
['Joe Jonas']
['Joe Keenan']
['Joe Klecko']
['Joe Knezevich']
['Joe Lando']
['Joe Letteri']
['Joe Lo Truglio']
['Joe Manganiello']
['Joe Mantegna']
['Joe Mantell']
['Joe Mantello']
['Joe Morton']
['Joe Nussbaum']
['Joe Odagiri']
['Joe Pantoliano']
['Joe Perrino']
['Joe Perry']
['Joe Pesci']
['Joe Piscopo']
['Joe Prospero']
['J

IOPub message rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_msg_rate_limit`.

Current values:
NotebookApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['Kathleen Robertson']
['Kathleen Rose Perkins']
['Kathleen Turner']
['Kathrine Narducci']
['Kathryn Bigelow']
['Kathryn Boyd']
['Kathryn Drysdale']
['Kathryn Erbe']
['Kathryn Hahn']
['Kathryn Harrold']
['Kathryn Joosten']
['Kathryn Layng']
['Kathryn Leigh Scott']
['Kathryn Lyn']
['Kathryn McCormick']
['Kathryn Morris']
['Kathryn Prescott']
['Kathryn Walker']
['Kathy Baker']
['Kathy Bates']
['Kathy Brier']
['Kathy Burke']
['Kathy Garver']
['Kathy Griffin']
['Kathy Hilton']
['Kathy Ireland']
['Kathy Kinney']
['Kathy Najimy']


KeyboardInterrupt: 

In [66]:
len(k[0][4][0])

460723